In [1]:
%matplotlib inline
import io, os, sys, types

# this import imports the databaseloader script (which only does TGSS and VLSSR for now)
import Databaseloader as dl
import loadinvizerfit as lif
import jsonwriter
import matplotlib
import loadjson as ljs
import matplotlib.pyplot as plt
import numpy as np
import scipy as sp
import tkp.db
from astropy.coordinates import SkyCoord
from tkp.db.model import Varmetric
from tkp.db.model import Runningcatalog
from tkp.db.model import Newsource
from tkp.db.model import Extractedsource
from tkp.db.model import Image
import operator
from operator import itemgetter, attrgetter

import logging
import pandas as pd
from pandas import DataFrame
import sqlalchemy
from sqlalchemy import *
from sqlalchemy.orm import relationship
#import Tools
#import generic_tools
#import plotting_tools
from scipy.stats import norm
import pylab
pylab.rcParams['legend.loc'] = 'best'
from matplotlib.ticker import NullFormatter
from matplotlib.font_manager import FontProperties
#from astroML import density_estimation

from scipy.cluster.hierarchy import dendrogram, linkage
from scipy.cluster.hierarchy import cophenet
from scipy.spatial.distance import pdist
from scipy.cluster.hierarchy import fcluster
from scipy.spatial import distance
import scipy.stats as ss
import scipy.optimize as op
import scipy.integrate as si
import sys
!{sys.executable} -m pip install numpy
!{sys.executable} -m pip install bokeh
from bokeh.plotting import figure, output_notebook, show
from bokeh.models import DatetimeTickFormatter
from bokeh.models import ColumnDataSource, Whisker
output_notebook()

logging.basicConfig(level=logging.INFO)

You are using pip version 9.0.1, however version 18.0 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.
You are using pip version 9.0.1, however version 18.0 is available.
You should consider upgrading via the 'pip install --upgrade pip' command.


Loading BokehJS ...

In [2]:
engine = 'postgresql'
host = 'vlo.science.uva.nl'
port = 5432
user = 'kmeulen'
password = 'kLu2oepRouv2UfoUPhoU'
database='KmeulenTrap4P23'
websiteURL = 'http://banana.transientskp.org/r4/vlo_'+database+'/runningcatalog/'
latexURL = '\url{http://banana.transientskp.org/r4/vlo_'+database+'/runningcatalog/'
latexHREF = '\href{http://banana.transientskp.org/r4/vlo_'+database+'/runningcatalog/'
query_loglevel = logging.WARNING  # Set to INFO to see queries, otherwise WARNING

In [3]:
# this is sqlalchemy script to login to the Banana database
logging.getLogger('sqlalchemy.engine').setLevel(query_loglevel)
db = tkp.db.Database(engine=engine, host=host, port=port,
                     user=user, password=password, database=database)
db.connect()
session = db.Session()

# Here i get the peak flux and the error on the peak flux from all the sources in the database
fpeak = session.query(Extractedsource.f_peak).all()
fpeake = session.query(Extractedsource.f_peak_err).all()
califreq = np.load("freqlist.npy")
califlux = np.load("fluxlist.npy")

INFO:tkp.db.database:Database config: postgresql://kmeulen@vlo.science.uva.nl:5432/KmeulenTrap4P23
/home/kmeulen/virtualenv/local/lib/python2.7/site-packages/psycopg2/__init__.py:144: UserWarning: The psycopg2 wheel package will be renamed from release 2.8; in order to keep installing from binary please use "pip install psycopg2-binary" instead. For details see: <http://initd.org/psycopg/docs/install.html#binary-install-from-pypi>.
  """)
INFO:tkp.db.database:connecting to database...
INFO:tkp.db.database:connected to: postgresql://kmeulen@vlo.science.uva.nl:5432/KmeulenTrap4P23


Query to find the variability parameters of the sources in a specific dataset 

In [4]:
# Here I specifiy which dataset of the database to use
dataset_id = 5
runcat_id = 16077

VarParams = session.query(Varmetric,Runningcatalog).select_from(join(Varmetric,Runningcatalog)).filter(Runningcatalog.dataset_id == dataset_id).all()

# VarFlux = session.query(Extractedsource).select_from(join(Extractedsource,Runningcatalog)).filter(Runningcatalog.dataset_id == dataset_id).all()



Make 2d array of all the sources except for the transients.

In [5]:

plotdata = [[VarParams[i].Runningcatalog.id, VarParams[i].Runningcatalog.wm_ra,\
             VarParams[i].Runningcatalog.wm_decl,VarParams[i].Runningcatalog.avg_ra_err,\
             VarParams[i].Runningcatalog.avg_decl_err, VarParams[i].Runningcatalog.datapoints,\
             session.query(Newsource).filter(Newsource.id==VarParams[i].Varmetric.newsource).one().newsource_type,\
             VarParams[i].Varmetric.newsource,VarParams[i].Varmetric.lightcurve_max,
             session.query(Newsource).filter(Newsource.id==VarParams[i].Varmetric.newsource).one().trigger_xtrsrc.id,VarParams[i].Varmetric.eta_int]\
            for i in range(len(VarParams)) if VarParams[i].Varmetric.newsource != None]


In [6]:
# The de Ruiter distance as shown in the Trap Paper section 4.4 https://arxiv.org/abs/1503.01526 

def CalcDeRuiter(transient,ra2,ra2e,dec2,dec2e):

    ra1 = transient['ra']
    dec1 = transient['dec']
    ra1e = transient['rae']
    dec1e = transient['dece']


    r=(np.sqrt((((-1*ra2 +ra1)**2)*(np.cos((dec1+dec2)/2))**2)/\
                       (ra1e**2+ra2e**2)+((-1*dec2+dec1)**2/(dec1e**2+dec2e**2))))
    return r 

In [7]:
# Comparing the fluxes heavily inspired on the de Ruiter distance as used by Bart's thesis: https://api-alumni.nl/media/uploads/theses/phd/lha-scheers-phd.pdf page 55

def CompareFluxes(transient,pflux2,pflux2e,scale=1):
    pflux1 = transient['pflux']*scale
    pflux1e = transient['pfluxe']*scale
    
    r = np.sqrt((((-1*pflux2 +pflux1)**2))/\
                       (pflux1e**2+pflux2e**2))
    return r

In [8]:
# calculates the frequency flux scale based on supplied califreq and califlux data

def CalcFreqScale(transient,datafreq,califreq,califlux):
    """Function for calculating the frequency scale"""
    transfreq = transient.freq
    for i in range(len(califreq)):
        if transfreq - 0.005 <= califreq[i] <= transfreq + 0.005:
            oldflux = califlux[i]
        if datafreq - 0.005 <= califreq[i] <= datafreq + 0.005:
            newflux = califlux[i]
    scale = newflux/oldflux
    return scale

def CalcRelFlux(transient,datafreq,dataflux):
    transfreq = transient.freq
    scale = np.power((transfreq/datafreq),-0.7)*dataflux 
    return scale

Left off here <a name='bookmark' />

Go to <a href=#bookmark2>my bookmark</a>



Function for pruning our candidate list

Function for comparing transient candidate against external databases

In [9]:

def CheckSimOutsideDatabase(data,sources,rcheck,ycheck,checklight,gamma,Cali,deruiter = True,euccutoff = 0.06):
    """ Function for checking against outside database the data entry is for the database rcheck is condition \
where we check deruiter against, ycheck is where we check de flux against and checklight,gamma,deruiter\
are booleans which switch on checking the flux(checklight), checking using error on the flux(gamma) and \
using deruiter distance

"""
    masterindex = []
    savedilist = []
    print 'before:'
    if Cali:
        scale =  CalcFreqScale(sources[0],data.freq,califreq,califlux)
    else:
        scale = CalcRelFlux(sources[0],data.freq,data.pflux)

    print len(sources)

    for i in sources:
        indexlist = []

        if not deruiter:
            Y = distance.cdist(i.radec,data.radec,'euclidean')
            if gamma:
                y = CompareFluxes(i,np.array(data.pflux),np.array(data.pfluxe),scale)
                
                for g in Y:

                    for j in range(len(g)):

                        if g[j] <=euccutoff and y[j]>= ycheck:
                            if i.id not in savedilist:
                                FluxVar(vars(i),j,data,scale)
                                savedilist.append(i.id)
                            indexlist.append(j)

                        elif g[j] <=euccutoff:
                            indexlist.append(j)
                    
            else:
                for g in Y:

                    for j in range(len(g)):
                        if checklight:

                            if g[j] <=euccutoff and (i.pflux*scale <= 0.9*data.pflux[j] or i.pflux*scale>=1.1*data.pflux[j]):
                                if i.id not in savedilist:
                                    FluxVar(vars(i),j,data,scale)
                                    savedilist.append(i.id)
                                indexlist.append(j)

                            elif g[j] <=euccutoff:
                                indexlist.append(j)
                        else:
                            if g[j] <=euccutoff:
                                indexlist.append(j)

        else:
            r = CalcDeRuiter(vars(i),np.array(data.ra),np.array(data.rae),np.array(data.dec),np.array(data.dece))
            if gamma:
                y = CompareFluxes(vars(i),np.array(data.pflux),np.array(data.pfluxe),scale)

                for j in range(len(r)):

                    if r[j] <=rcheck:
                        indexlist.append([j,r[j]])
               
                if checklight and indexlist:
                    pfluxlist = []
                    pfluxelist = []
                    
                    indexvalue = np.argmin(np.array(indexlist)[:,1])
                    pfluxlist.append(data.pflux[indexlist[indexvalue][0]])
                    pfluxelist.append(data.pfluxe[indexlist[indexvalue][0]])
                    
                    y = CompareFluxes(vars(i),np.array(pfluxlist),np.array(pfluxelist))

                    
                    if y[0]>=ycheck:
                        print indexlist[indexvalue][0]
                        FluxVar(vars(i),indexlist[indexvalue][0],data,scale)
#                     for z in indexlist:
# #                         print '--------------'
# #                         print i.ra
# #                         print i.dec
# #                         print data.ra[z]
# #                         print data.dec[z]
# #                         print data.pflux[z]
# #                         print '___________'
# #                         print np.argmin(z[1])
#                         pfluxlist.append(data.pflux[z[0]])
#                         pfluxelist.append(data.pfluxe[z[0]])

#                     y = CompareFluxes(vars(i),np.array(pfluxlist),np.array(pfluxelist))
                    
#                     for o in range(len(y)):
#                         if y[o]>=ycheck:
#                             print indexlist[o][0]
#                             FluxVar(vars(i),indexlist[o][0],data,scale)
#                             break

            else:
                for j in range(len(r)):
                    if checklight:
                        if r[j] <=rcheck and (i.pflux*scale <= 0.9*data.pflux[j] or i.pflux*scale>=1.1*data.pflux[j]):
                            indexlist.append(j)
                            if i.id not in savedilist:
                                FluxVar(vars(i),j,data,scale)
                                savedilist.append(i.id)
                        elif r[j] <=rcheck:
                            indexlist.append(j)





                    else:
                        if r[j] <=rcheck:
                            indexlist.append(j)

        masterindex.append(indexlist)
    
#     check if thereis a zero listentry in masterindex.. if so append it to the varying pos sources class.
    i = 0
    while i < len(masterindex):
        if not masterindex[i]:
            PosVar(vars(sources[i]),data)
        i+=1

    print 'after:'  
    print str(len(PosVar.instances)) +" Interesting candidates"
    print str(len(FluxVar.instances)) + " Flux Varying candidates"


Class object for saving our candidate transients, class object for storing objects that have varying flux compared to external database and
Initialize our transients class and other banana sources lists.

(This piece of code has to be rerun everytime you adjust something)

In [10]:

class Transients(object):
    instances = []
    def __init__(self,ra,rae,dec,dece,ids,pflux,pfluxe):
        self.id = ids
        y = np.stack((ra,dec),axis = -1)
        self.ra = ra
        self.rae = rae
        self.dec = dec
        self.dece = dece
        self.pflux = pflux
        self.pfluxe = pfluxe
        self.freq = 144
        self.keys = ['yoloswag']
        self.radec = np.reshape(y,(1,2))
        c = SkyCoord(self.ra, self.dec, frame='fk5', unit='deg')
        self.fk5 = c.to_string('hmsdms',sep=' ',precision= 0)
        Transients.instances.append(self)

    def DelFalse(i):
        del Transients.instances[i]

class PosVar(object):
    """class object for storing objects that have a varying position compared to the database we are looking in"""
    instances = []
    def __init__(self,params,database):
        self.id = params['id']            
        self.ra = params['ra']
        self.database = database
        self.dataname = database.name
        self.dec = params['dec']
        self.radec = params['radec']
        self.pflux = params['pflux']
        c = SkyCoord(params['ra'], params['dec'], frame='fk5', unit='deg')
        self.fk5 = c.to_string('hmsdms',sep=' ',precision= 0)
        try:
            self.iflux = params['iflux']
        except:
            pass
        PosVar.instances.append(self)
        

class TestInstance(object):
    """class object for storing objects that have a varying position compared to the database we are looking in"""
    instances = []
    def __init__(self,params):
        self.id = params['id']            
        self.ra = params['ra']
        self.dec = params['dec']
        self.rae = params['rae']
        self.dece = params['dece']
        self.radec = params['radec']
        self.pflux = params['pflux']
        self.freq = params['freq']
        self.pfluxe = params['pfluxe']
        c = SkyCoord(params['ra'], params['dec'], frame='fk5', unit='deg')
        self.fk5 = c.to_string('hmsdms',sep=' ',precision= 0)
        try:
            self.iflux = params['iflux']
        except:
            pass
        TestInstance.instances.append(self)
        
class SavedFluxSources(object):
    """class object for storing objects that have a varying position compared to the database we are looking in"""
    instances = []
    def __init__(self,initialid,initialpflux,initialpfluxerr,params):
        self.id = params['id']            
        self.ra = params['ra']
        self.dec = params['dec']
        self.rae = params['rae']
        self.dece = params['dece']
        self.radec = params['radec']
        self.pflux = params['pflux']
        self.freq = params['freq']
        self.pfluxe = params['pfluxe']
        c = SkyCoord(params['ra'], params['dec'], frame='fk5', unit='deg')
        self.fk5 = c.to_string('hmsdms',sep=' ',precision= 0)
        self.cmpid = initialid
        self.cmppflux = initialpflux
        self.cmppfluxerr = initialpfluxerr
        try:
            self.iflux = params['iflux']
        except:
            pass
        SavedFluxSources.instances.append(self)

class SavedPosSources(object):
    """class object for storing objects that have a varying position compared to the database we are looking in"""
    instances = []
    def __init__(self,params):
        self.id = params['id']            
        self.ra = params['ra']
        self.dec = params['dec']
        self.rae = params['rae']
        self.dece = params['dece']
        self.radec = params['radec']
        self.pflux = params['pflux']
        self.freq = params['freq']
        self.pfluxe = params['pfluxe']
        c = SkyCoord(params['ra'], params['dec'], frame='fk5', unit='deg')
        self.fk5 = c.to_string('hmsdms',sep=' ',precision= 0)
        try:
            self.iflux = params['iflux']
        except:
            pass
        SavedPosSources.instances.append(self)  
    
class FluxVar(object):
    """class object for storing objects that have a varying flux compared to the database we are looking in"""
    instances = []
    def __init__(self,params,databaseentry,database,scale):
        self.id = params['id']
        self.ra = params['ra']
        self.database = database
        self.dataname = database.name
        self.scale = scale
        self.dec = params['dec']
        self.radec = params['radec']
        self.pflux = params['pflux']
        self.entry = databaseentry
        c = SkyCoord(params['ra'], params['dec'], frame='fk5', unit='deg')
        self.fk5 = c.to_string('hmsdms',sep=' ',precision= 0)
        c = c.icrs
        self.icrs = c.to_string('hmsdms',sep=' ',precision= 0)
        try:
            self.iflux = params['iflux']
        except:
            pass
        FluxVar.instances.append(self)
    

        
racata = []
raecata = []
deccata = []
dececata = []
idcata = []
lightcata = []
lightecata = []
for i in range(len(plotdata)):
    if plotdata[i][6] == 1:
        Transients(plotdata[i][1],plotdata[i][3],plotdata[i][2],plotdata[i][4],plotdata[i][0],fpeak[plotdata[i][9]-1][0],fpeake[plotdata[i][9]-1][0])
    else:
        racata.append(plotdata[i][1])
        raecata.append(plotdata[i][3])
        deccata.append(plotdata[i][2])
        dececata.append(plotdata[i][4])
        idcata.append(plotdata[i][0])
        lightcata.append(fpeak[plotdata[i][9]-1][0])
        lightecata.append(fpeake[plotdata[i][9]-1][0])
X = np.stack((racata,deccata),axis = -1)

racata = np.array(racata)
raecata = np.array(raecata)
dececata = np.array(dececata)
deccata = np.array(deccata)
idcata = np.array(idcata)
lightcata = np.array(lightcata)
lightecata = np.array(lightecata)


# Transients(183,0.01,45,0.01,99999999,1.32,0.001)

In [11]:
rasl = []
raesl = []
decsl = []
decesl = []
idsl = []
pfluxsl = []
pfluxesl = []
for i in range(len(plotdata)):
    rasl.append(plotdata[i][1])
    raesl.append(plotdata[i][3])
    decsl.append(plotdata[i][2])
    decesl.append(plotdata[i][4])
    idsl.append(plotdata[i][0])
    pfluxsl.append(fpeak[plotdata[i][9]-1][0])
    pfluxesl.append(fpeake[plotdata[i][9]-1][0])



raseries = pd.Series(racata)
raseries
ras = pd.Series(rasl, name='ra')
raes = pd.Series(raesl, name='raerr')
decs = pd.Series(decsl, name='dec')
deces = pd.Series(decesl, name='decerr')
ids = pd.Series(idsl, name='id')
pfluxs = pd.Series(pfluxsl, name='pflux')
pfluxes = pd.Series(pfluxesl, name='pfluxerr')

pandacata = pd.concat([ras, raes,decs,deces,ids,pfluxs,pfluxes], axis=1)


here we call the function for calculating the de ruiter distance between candidates and our found sources and if True is given we also check if the max of the lightcurve of the sources compared fall withing 5 sigma flux of each other (thus making it increasingly likely for   the source to be a sidelobe)

This extra flux comparison is used in order to not potentially write of a faint or bright transient close to a known source.

In [12]:
def SelectorForCandidateslist(rcheck,ycheck,checklight,deruiter=True):
    """Function for pruning the candidate list using both distance and lightcurve measurements"""
    ctr = 0
    print 'before:'
    print len(Transients.instances)
    oldlen = len(Transients.instances) + 1
    
# #   Repeat until no improvement in the length of the candidate list
#     while len(Transients.instances) - oldlen < 0:
    ratlist = []
    detclist = []

    translist = []
#         rlist = []
    oldlen = len(Transients.instances)

#         These lists are necessary to compare the candidate Transientss against each other
    ralist = []
    raelist = []
    declist = []
    decelist = []

# """Check candidate Transientss against each other"""

    for h in Transients.instances:
        if not deruiter:
            translist.append(h.radec)
        else:
            ralist.append(h.ra)
            raelist.append(h.rae)
            declist.append(h.dec)
            decelist.append(h.dece)
            

    masterindex = []
    savedlist = []
    first = True
    for i in Transients.instances:
        nocount = False
        indexlist = []


# #             again the outdated euclidean method
#         if not deruiter:
#             Y = distance.cdist(i.radec,X,'euclidean')

#             for g in Y:
#                 for j in range(len(g)):
#                     if checklight:
#                         if g[j] <=0.06 and 0.8*lightcata[j]<=i.pflux <= 1.2*lightcata[j]:
#                             indexlist.append(j)
#                     else:
#                         if g[j] <=0.06:
#                             indexlist.append(j)

#             the de Ruiter method 
#         else:
        r = CalcDeRuiter(vars(i),np.array(ralist),\
        np.array(raelist),np.array(declist),np.array(decelist))
        y = CompareFluxes(vars(i),np.array(lightcata),np.array(lightecata))
        for j in range(len(r)):

            if r[j] <=rcheck and r[j]!=0.0:
                indexlist.append(j)
                nocount = True
                        
#         SAVE ENTRIES THAT HAVE A BIG DIFFERENCE ON FLUX
        if checklight:
            pfluxlist = []
            pfluxelist = []
            for z in indexlist:            
                pfluxlist.append(Transients.instances[z].pflux)
                pfluxelist.append(Transients.instances[z].pfluxe)

            y = CompareFluxes(vars(i),np.array(pfluxlist),np.array(pfluxelist))
            
            if first:
                print y
                first = False
                try:
                    print Transients.instances[indexlist[0]].id
                except:
                    pass
            for o in range(len(y)):
                if y[o]>=ycheck:
                    SavedFluxSources(i.id,i.pflux,i.pfluxe,vars(Transients.instances[indexlist[o]]))
                    break
                    
                 
#         DELETE DOUBLE ENTRIES reform lists
        if nocount:
            k = 0
            g = 0
            while k < len(indexlist):
                del Transients.instances[indexlist[k]-g]

                k+=1
                g+=1

            ralist = []
            raelist = []
            declist = []
            decelist = []

            for h in Transients.instances:
                ralist.append(h.ra)
                raelist.append(h.rae)
                declist.append(h.dec)
                decelist.append(h.dece)


    print 'after:'
#     add back the no duplicate detections
#     for i in SavedPosSources.instances:
#         TestInstance(vars(i))
    print len(Transients.instances)
    print len(SavedFluxSources.instances)



In [13]:
SelectorForCandidateslist(rcheck = 3, ycheck = 3,checklight = True, deruiter = True)


before:
602
[72.40047787 66.67361514 73.49158554  8.98839618  7.60474333 10.56913633
 74.32682577 62.16881908  6.09566687 10.12399222  2.30997548 10.40042313
 13.51870588 73.09609369  7.34464434 10.59262606 76.8032959   6.27464459
 71.31617417  1.64595361 72.85310593 78.80836623  9.4549157  66.28679245
 79.32491235 78.35575131 77.22965829 11.28355494 69.44672618  3.39277634
 70.23387871]
15380
after:
50
37


print out in latex format:

In [14]:
try:
    print SavedFluxSources.instances[0].pflux
    print Transients.instances[0].pflux
except:
    pass
FluxVar.instances = []
PosVar.instances = []

0.717379657755
7.18846941692


Go to <a href=#bookmark>my bookmark</a>
Left off here <a name='bookmark2' />

# tgss 
is the object which has tggs survey data for the field of P23 loaded into it.
could probably just automate it here but lets leave it for now

In [15]:
tgsslist = dl.ReadData("tgss")
tgss = tgsslist[1]
print tgss.keys
print tgss.freq
print tgss.name
print len(tgss.ra)
print np.mean(tgss.rae)

['name', 'radec', 'ra', 'rae', 'dec', 'dece', 'pflux', 'pfluxe', 'freq']
147.5
tgss
98604
0.0006028485434442595


In [16]:
CheckSimOutsideDatabase(tgss,Transients.instances,rcheck = 3,ycheck = 3,\
                     checklight = True, gamma = True,Cali = True,deruiter = True,euccutoff = .06)

before:
50
249
802
1062
346
123
388
976
809
753
246
1072
1085
after:
5 Interesting candidates
12 Flux Varying candidates


In [17]:
print Transients.instances[0].fk5


12 22 52 +50 26 56


## VLSSr

In [18]:
# TODO fix the error for the vlssr data
 
# Probably need to pip install xlrd for excell support in pandas
vlssr = dl.ReadData('vlssr')[0]

print vlssr.keys
print vlssr.freq
print vlssr.ra

vlssrdataset.xls
*** No CODEPAGE record, no encoding_override: will use 'ascii'
*** No CODEPAGE record, no encoding_override: will use 'ascii'
*** No CODEPAGE record, no encoding_override: will use 'ascii'
*** No CODEPAGE record, no encoding_override: will use 'ascii'
['name', 'radec', 'ra', 'rae', 'dec', 'dece', 'pflux', 'pfluxe', 'freq']
74
[185.2953 184.7767 185.0477 ... 214.8349 165.3226 213.6304]


In [19]:

CheckSimOutsideDatabase(vlssr,Transients.instances,rcheck = 3 ,ycheck = 3,checklight = True,\
                     gamma = True,Cali=True,deruiter = True,euccutoff = 0.06)

before:
50
48
1
209
155
0
44
56
50
19
77
170
236
26
85
18
84
107
76
215
60
89
211
52
82
73
98
173
127
42
68
46
116
238
74
240
after:
10 Interesting candidates
47 Flux Varying candidates


In [20]:

savedpos = []
savedflux = []
print len(PosVar.instances)
print len(FluxVar.instances)
for i in PosVar.instances:
    if i.id not in savedpos:
        savedpos.append(i.id)
for i in FluxVar.instances:
    if i.id not in savedflux:
        savedflux.append(i.id)
        
print len(savedpos)
print len(savedflux)

10
47
5
37


## Print saved flux sources LATEX

In [21]:
print "\\begin{longtable}{c|c|c|c|c|c|c|c|c|c} \n\
\\toprule \n Id & Ra (deg) & Dec (deg) & Fk5 & Flux & Fluxerr & cmpId & cmpFlux & cmpFluxerr & Candidate? (y/n)  \\\\\\midrule \n\\endfirsthead \n\\toprule \
\n Id & Ra (deg) & Dec (deg) & Fk5 & Flux & Fluxerr & cmpId & cmpFlux & cmpFluxerr & Candidate? (y/n)  \\\\\\midrule \n\\endhead \n\\bottomrule \n\\endfoot \n\\bottomrule"

# define caption for table
print "\\caption{ SAVED FLUX SOURCES} \n\\endlastfoot"
for i in SavedFluxSources.instances:
    print latexHREF + str(i.id) +"}{%i}" %(i.id)+ " " + "&"+ " " + '%0.3f' %i.ra + " " + "&"+ " "+ "%0.3f" %(i.dec) +\
    " " + "&" + i.fk5+"&" + " " + '%0.3f' %(i.pflux) +"&" + " " + '%0.3f' %(i.pfluxe) +"&" + " " +\
    latexHREF + str(i.cmpid) +"}{%i}" %(i.cmpid)\
    +"&" + " " +'%0.3f' %(i.cmppflux) +"&" + " "\
    + '%0.3f' %(i.cmppfluxerr) +"&" + " " +"\\" + "\\"
print "\\end{longtable}"

\begin{longtable}{c|c|c|c|c|c|c|c|c|c} 
\toprule 
 Id & Ra (deg) & Dec (deg) & Fk5 & Flux & Fluxerr & cmpId & cmpFlux & cmpFluxerr & Candidate? (y/n)  \\\midrule 
\endfirsthead 
\toprule 
 Id & Ra (deg) & Dec (deg) & Fk5 & Flux & Fluxerr & cmpId & cmpFlux & cmpFluxerr & Candidate? (y/n)  \\\midrule 
\endhead 
\bottomrule 
\endfoot 
\bottomrule
\caption{ SAVED FLUX SOURCES} 
\endlastfoot
\href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/15380}{15380} & 185.695 & 50.465 &12 22 47 +50 27 53& 0.717& 0.066& \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/16077}{16077}& 7.188& 0.061& \\
\href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/13300}{13300} & 184.777 & 48.499 &12 19 06 +48 29 56& 0.770& 0.004& \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/15556}{15556}& 0.819& 0.005& \\
\href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/12626}{12626} & 188.278 & 45.483 &1

# Print the same position Fluxvariating sources

In [22]:
for i in FluxVar.instances:
    
    print "Data compared to " + i.database.name
    print i.id
    print websiteURL+str(i.id)
    print 'bananaflux: ' + str(i.pflux*i.scale)

    print i.database.name+'flux: ' + str(i.database.pflux[i.entry])
    print i.database.ra[i.entry]
    print i.database.dec[i.entry]
    print "------------------------"
        
#     if i.database == 'vssr':
        
#         print 'bananaflux: ' + str(i.pflux * vlssrscale)
#         print 'vlssrflux: ' + str(vssr.pflux[i.entry])
#         print "########################"
#     print vssr.ra[i.entry]
#     print vssr.dec[i.entry]
#     print i.ra
#     print i.dec

Data compared to tgss
16077
http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/16077
bananaflux: 7.06905613895605
tgssflux: 5.4003000000000005
185.71597
50.44842
------------------------
Data compared to tgss
7308
http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/7308
bananaflux: 0.7316127864414221
tgssflux: 1.3365
182.76134
45.65354
------------------------
Data compared to tgss
8741
http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/8741
bananaflux: 0.938806784001484
tgssflux: 2.3371
185.79407
44.59548
------------------------
Data compared to tgss
10309
http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/10309
bananaflux: 0.9004814823173248
tgssflux: 0.6698999999999999
185.36694
50.8145
------------------------
Data compared to tgss
12944
http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/12944
bananaflux: 1.5521627763364672
tgssflux: 3.7626999999999997
183.37238
48.38688
----------------------

# Print the same position Fluxvariating sources in Latex ready format

In [23]:

# SEPERATE DATABASES
databaselist = ['tgss','vlssr']

samesieslist = []
for i in range(len(FluxVar.instances)):
    samesie = False
    tempdict = {'tgss':None,'vlssr':None,'id':None,'ra':None,'dec':None,'fk5':None}
    
#   create combined name if entry both in vlssr and tgss
    for j in range(len(samesieslist)):
        if FluxVar.instances[i].id == samesieslist[j]['id']:
#             samesieslist[j].append(FluxVar.instances[i])
            samesieslist[j][FluxVar.instances[i].database.name] = FluxVar.instances[i]
          
            samesie = True
    if not samesie:
        tempdict[FluxVar.instances[i].database.name] = FluxVar.instances[i]
        tempdict['id'] = FluxVar.instances[i].id
        tempdict['ra'] = FluxVar.instances[i].ra
        tempdict['dec'] = FluxVar.instances[i].dec
        tempdict['fk5'] = FluxVar.instances[i].fk5
        samesieslist.append(tempdict)


print "\\begin{longtable}{c|c|c|c|c|c|c|c|c|c|c|c|c} \n\
\\toprule \nFlux147.5MHz (Jy) & Tgss (Jy) & Flux74MHz (Jy)& Vlssr (Jy) & fk5 & Ra (deg) & Dec (deg) &tggsRa&tgssDec&\
vlssrRa&vlssrDec& Id/Link & (y/n)  \\\\\\midrule \n\\endfirsthead \n\\toprule \
\nFlux147.5MHz (Jy) & Tgss (Jy) & Flux74MHz (Jy)& Vlssr (Jy)& fk5 & Ra (deg) & Dec (deg)  &tggsRa&tgssDec&\
vlssrRa&vlssrDec& Id/Link & (y/n) \\\\\\midrule \n\\endhead \n\\bottomrule \n\\endfoot \n\\bottomrule"

# define caption for table
print "\\caption{ Comparison of variable fluxes with the same position for different databases 1hr} \n\\endlastfoot"
lastname = None
# samesieslist = sorted(samesieslist, key=lambda e: (e['ra'], e['dec']))
for i in samesieslist:
    a= ''
    b=''
    for j in(databaselist):
        try: 
            a+= str(np.around(i[j].pflux*i[j].scale,3)) + " " + "&"+ " "
        except:
            a += "-" +" "+ "&"+ " "
        try:
            a+= str(np.around(i[j].database.pflux[i[j].entry],3)) + " " + "&"+ " "   
        except:
            a += "-" +" "+ "&"+ " "
            
        try: 
            b+= '%0.3f' %(i[j].database.ra[i[j].entry])+" "+"&"+" "
            b+= '%0.3f' %(i[j].database.dec[i[j].entry])+" "+"&"+" "
        except:
            b+= "-" + " " + "&"+" " "-" + " " + "&"+" "
        
    a +=i['fk5'] + " " + '&' + "  "+ '%0.3f' %i['ra'] + " " + "&"+ " "+ "%0.3f" %i['dec'] \
    + " " + '&' + "  "+ b+ latexHREF +str(i["id"])+"}" + "{%i}" %i['id'] +" "+"&"+" "+  "\\" + "\\"
    print a

print "\\end{longtable}"

\begin{longtable}{c|c|c|c|c|c|c|c|c|c|c|c|c} 
\toprule 
Flux147.5MHz (Jy) & Tgss (Jy) & Flux74MHz (Jy)& Vlssr (Jy) & fk5 & Ra (deg) & Dec (deg) &tggsRa&tgssDec&vlssrRa&vlssrDec& Id/Link & (y/n)  \\\midrule 
\endfirsthead 
\toprule 
Flux147.5MHz (Jy) & Tgss (Jy) & Flux74MHz (Jy)& Vlssr (Jy)& fk5 & Ra (deg) & Dec (deg)  &tggsRa&tgssDec&vlssrRa&vlssrDec& Id/Link & (y/n) \\\midrule 
\endhead 
\bottomrule 
\endfoot 
\bottomrule
\caption{ Comparison of variable fluxes with the same position for different databases 1hr} 
\endlastfoot
7.069 & 5.4 & 11.179 & 9.248 & 12 22 52 +50 26 56 &  185.716 & 50.449 &  185.716 & 50.448 & 185.716 & 50.451 & \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/16077}{16077} & \\
0.732 & 1.336 & 1.157 & 2.031 & 12 11 03 +45 39 05 &  182.764 & 45.651 &  182.761 & 45.654 & 182.760 & 45.653 & \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/7308}{7308} & \\
0.939 & 2.337 & 1.485 & 3.276 & 12 23 12 +44 36 00 &  185.

# Print the Position variating sources in Latex ready format

In [24]:
# SEPERATE DATABASES

print "\\begin{longtable}{c|c|c|c|c|c} \n\
\\toprule \nDatabase & Ra (deg) & Dec (deg) & Fk5 & Id/Link & Candidate? (y/n)  \\\\\\midrule \n\\endfirsthead \n\\toprule \
\nDatabase & Ra (deg) & Dec (deg) & Fk5 & Id/Link & Candidate? (y/n)  \\\\\\midrule \n\\endhead \n\\bottomrule \n\\endfoot \n\\bottomrule"

# define caption for table
print "\\caption{ Comparison position of candidates with different databases for the 10 min interval data} \n\\endlastfoot"
lastname = None
for i in PosVar.instances:
    if i.database.name != lastname and lastname:
        print "\\hline"
    print i.database.name +" "+ "&"+ " " + '%0.3f' %i.ra + " " + "&"+ " "+ "%0.3f" %i.dec +\
    " " + "&" + " " + i.fk5 +" " + '&' + "  "+ latexHREF +str(i.id)+"}" + "{%i}" %i.id +" " + '&' + "  "+"\\" + "\\"
    
    lastname = i.database.name

print "\\end{longtable}"

\begin{longtable}{c|c|c|c|c|c} 
\toprule 
Database & Ra (deg) & Dec (deg) & Fk5 & Id/Link & Candidate? (y/n)  \\\midrule 
\endfirsthead 
\toprule 
Database & Ra (deg) & Dec (deg) & Fk5 & Id/Link & Candidate? (y/n)  \\\midrule 
\endhead 
\bottomrule 
\endfoot 
\bottomrule
\caption{ Comparison position of candidates with different databases for the 10 min interval data} 
\endlastfoot
tgss & -175.262 & 50.444 & 12 18 57 +50 26 37 &  \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/16306}{16306} &  \\
tgss & -174.211 & 44.590 & 12 23 09 +44 35 24 &  \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/16326}{16326} &  \\
tgss & -171.721 & 45.481 & 12 33 07 +45 28 52 &  \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/16375}{16375} &  \\
tgss & -173.524 & 44.939 & 12 25 54 +44 56 22 &  \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/16130}{16130} &  \\
tgss & -176.475 & 50.479 & 12 14 06 +50

In [25]:
# COMBINED DATABASES (SLOWER)

samesieslist = []
for i in range(len(PosVar.instances)):
    samesie = False
    
#   create combined name if entry both in vlssr and tgss
    for j in range(len(samesieslist)):
        if PosVar.instances[i].id == samesieslist[j][0]:
            samesieslist[j][1] = samesieslist[j][1] + " \& " + PosVar.instances[i].database.name
            samesie = True
    if not samesie:
        samesieslist.append([PosVar.instances[i].id,PosVar.instances[i].database.name,PosVar.instances[i]])
    
samesieslist = sorted(samesieslist, key=itemgetter(1))

print "\\begin{longtable}{c|c|c|c|c|c} \n\
\\toprule \nDatabase & Ra (deg) & Dec (deg)& Fk5 & Id/Link & Candidate? (y/n)  \\\\\\midrule \n\\endfirsthead \n\\toprule \
\nDatabase & Ra (deg) & Dec (deg) & Fk5 &Id/Link & Candidate? (y/n)  \\\\\\midrule \n\\endhead \n\\bottomrule \n\\endfoot \n\\bottomrule"

# define caption for table
print "\\caption{ Comparison position of candidates with different databases for the 1hr interval data} \n\\endlastfoot"
lastname = None
for i in samesieslist:
    if i[1] != lastname and lastname:
        print "\\hline"
    print i[1] +" "+ "&"+ " "+ '%0.3f' %i[2].ra + " " + "&"+ " "+ "%0.3f" %(i[2].dec) +\
    " " + "&" + " " +i[2].fk5 +" " + '&' + "  "+ latexHREF +str(i[0])+"}" + "{%i}" %i[0] +" " + '&' + "  "+"\\" + "\\"
    
    lastname = i[1]

print "\\end{longtable}"

\begin{longtable}{c|c|c|c|c|c} 
\toprule 
Database & Ra (deg) & Dec (deg)& Fk5 & Id/Link & Candidate? (y/n)  \\\midrule 
\endfirsthead 
\toprule 
Database & Ra (deg) & Dec (deg) & Fk5 &Id/Link & Candidate? (y/n)  \\\midrule 
\endhead 
\bottomrule 
\endfoot 
\bottomrule
\caption{ Comparison position of candidates with different databases for the 1hr interval data} 
\endlastfoot
tgss \& vlssr & -175.262 & 50.444 & 12 18 57 +50 26 37 &  \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/16306}{16306} &  \\
tgss \& vlssr & -174.211 & 44.590 & 12 23 09 +44 35 24 &  \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/16326}{16326} &  \\
tgss \& vlssr & -171.721 & 45.481 & 12 33 07 +45 28 52 &  \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/16375}{16375} &  \\
tgss \& vlssr & -173.524 & 44.939 & 12 25 54 +44 56 22 &  \href{http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/16130}{16130} &  \\
tgss \& 

In [26]:
jsonwriter.WriteFluxJson(FluxVar.instances)

In [27]:
try:
    os.remove('neat.json')
except:
    print 'allready removed'
!{sys.executable} -m scrapy runspider scrapper.py -o neat.json
dfFlux = ljs.Loadin()

/home/kmeulen/virtualenv/local/lib/python2.7/site-packages/cryptography/hazmat/primitives/constant_time.py:26: CryptographyDeprecationWarning: Support for your Python version is deprecated. The next version of cryptography will remove support. Please upgrade to a 2.7.x release that supports hmac.compare_digest as soon as possible.
  utils.DeprecatedIn23,
2018-09-21 17:42:25 [scrapy.utils.log] INFO: Scrapy 1.5.1 started (bot: scrapybot)
2018-09-21 17:42:25 [scrapy.utils.log] INFO: Versions: lxml 4.2.5.0, libxml2 2.9.8, cssselect 1.0.3, parsel 1.5.0, w3lib 1.19.0, Twisted 18.7.0, Python 2.7.6 (default, Nov 23 2017, 15:49:48) - [GCC 4.8.4], pyOpenSSL 18.0.0 (OpenSSL 1.1.0i  14 Aug 2018), cryptography 2.3.1, Platform Linux-3.13.0-141-generic-x86_64-with-Ubuntu-14.04-trusty
2018-09-21 17:42:25 [scrapy.crawler] INFO: Overridden settings: {'SPIDER_LOADER_WARN_ONLY': True, 'FEED_FORMAT': 'json', 'FEED_URI': 'neat.json'}
2018-09-21 17:42:25 [scrapy.middleware] INFO: Enabled extensions:
['scrapy

2018-09-21 17:42:26 [scrapy.core.engine] DEBUG: Crawled (200) <POST http://vizier.u-strasbg.fr/viz-bin/VizieR-4> (referer: http://vizier.u-strasbg.fr/viz-bin/VizieR-3?-source=VIII/85A/spectra&-c=186.0573%2B46.3355&-c.u=arcsec&-c.r=5&-out.add=_r&-sort=_r)
2018-09-21 17:42:26 [scrapy.core.engine] DEBUG: Crawled (200) <POST http://vizier.u-strasbg.fr/viz-bin/VizieR-4> (referer: http://vizier.u-strasbg.fr/viz-bin/VizieR-3?-source=VIII/85A/spectra&-c=185.7162%2B50.4489&-c.u=arcsec&-c.r=5&-out.add=_r&-sort=_r)
2018-09-21 17:42:26 [scrapy.core.engine] DEBUG: Crawled (200) <POST http://vizier.u-strasbg.fr/viz-bin/VizieR-4> (referer: http://vizier.u-strasbg.fr/viz-bin/VizieR-3?-source=VIII/85A/spectra&-c=185.8014%2B44.6000&-c.u=arcsec&-c.r=5&-out.add=_r&-sort=_r)
2018-09-21 17:42:26 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'6612', 'e': u'6.6e+01', 'nu': u'325', 's_nu': u'3.28e+02'}
2018-09-21 17:42:26 [scrapy.core.scraper] DEBUG: Scrape

2018-09-21 17:42:27 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'15556', 'e': u'1.3e+02', 'nu': u'8400', 's_nu': u'6.57e+02'}
2018-09-21 17:42:27 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'15556', 'e': u'1.4e+02', 'nu': u'1400', 's_nu': u'6.77e+02'}
2018-09-21 17:42:27 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'15556', 'e': u'1.6e+02', 'nu': u'151', 's_nu': u'8.11e+02'}
2018-09-21 17:42:27 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'15556', 'e': u'1.4e+02', 'nu': u'8400', 's_nu': u'6.76e+02'}
2018-09-21 17:42:27 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'15556', 'e': u'1.3e+02', 'nu': u'8400', 's_nu': u'6.59e+02'}
2018-09-21 17:42:27 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.

2018-09-21 17:42:27 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'6567', 'e': u'1.9e+01', 'nu': u'1400', 's_nu': u'9.59e+01'}
2018-09-21 17:42:27 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'6567', 'e': u'1.9e+01', 'nu': u'1400', 's_nu': u'9.62e+01'}
2018-09-21 17:42:27 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'6567', 'e': u'7.4e+01', 'nu': u'325', 's_nu': u'3.69e+02'}
2018-09-21 17:42:27 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'6567', 'e': u'1.7e+02', 'nu': u'74', 's_nu': u'8.60e+02'}
2018-09-21 17:42:27 [scrapy.core.engine] DEBUG: Crawled (200) <POST http://vizier.u-strasbg.fr/viz-bin/VizieR-4> (referer: http://vizier.u-strasbg.fr/viz-bin/VizieR-3?-source=VIII/85A/spectra&-c=181.7589%2B48.0319&-c.u=arcsec&-c.r=5&-out.add=_r&-sort=_r)
2018-09-21 17:42:27 [scr

2018-09-21 17:42:28 [scrapy.core.engine] DEBUG: Crawled (200) <POST http://vizier.u-strasbg.fr/viz-bin/VizieR-4> (referer: http://vizier.u-strasbg.fr/viz-bin/VizieR-3?-source=VIII/85A/spectra&-c=183.7918%2B46.4543&-c.u=arcsec&-c.r=5&-out.add=_r&-sort=_r)
2018-09-21 17:42:28 [scrapy.core.engine] DEBUG: Crawled (200) <POST http://vizier.u-strasbg.fr/viz-bin/VizieR-4> (referer: http://vizier.u-strasbg.fr/viz-bin/VizieR-3?-source=VIII/85A/spectra&-c=188.5862%2B49.2407&-c.u=arcsec&-c.r=5&-out.add=_r&-sort=_r)
2018-09-21 17:42:28 [scrapy.core.engine] DEBUG: Crawled (200) <POST http://vizier.u-strasbg.fr/viz-bin/VizieR-4> (referer: http://vizier.u-strasbg.fr/viz-bin/VizieR-3?-source=VIII/85A/spectra&-c=181.3022%2B48.2980&-c.u=arcsec&-c.r=5&-out.add=_r&-sort=_r)
2018-09-21 17:42:28 [scrapy.core.engine] DEBUG: Crawled (200) <POST http://vizier.u-strasbg.fr/viz-bin/VizieR-4> (referer: http://vizier.u-strasbg.fr/viz-bin/VizieR-3?-source=VIII/85A/spectra&-c=185.5330%2B46.7547&-c.u=arcsec&-c.r=5&-o

2018-09-21 17:42:28 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'7967', 'e': u'1.1e+02', 'nu': u'365', 's_nu': u'5.55e+02'}
2018-09-21 17:42:28 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'7967', 'e': u'3.2e+02', 'nu': u'151', 's_nu': u'1.62e+03'}
2018-09-21 17:42:28 [scrapy.core.engine] DEBUG: Crawled (200) <POST http://vizier.u-strasbg.fr/viz-bin/VizieR-4> (referer: http://vizier.u-strasbg.fr/viz-bin/VizieR-3?-source=VIII/85A/spectra&-c=183.0110%2B46.9372&-c.u=arcsec&-c.r=5&-out.add=_r&-sort=_r)
2018-09-21 17:42:28 [scrapy.core.engine] DEBUG: Crawled (200) <POST http://vizier.u-strasbg.fr/viz-bin/VizieR-4> (referer: http://vizier.u-strasbg.fr/viz-bin/VizieR-3?-source=VIII/85A/spectra&-c=183.5239%2B50.4794&-c.u=arcsec&-c.r=5&-out.add=_r&-sort=_r)
2018-09-21 17:42:28 [scrapy.core.scraper] DEBUG: Scraped from <200 http://vizier.u-strasbg.fr/viz-bin/VizieR-4>
{'id': u'7890', 'e

In [28]:

# models to try
def starmodel(value,a,b,c):
    return a*value**-b+c

def starmodel2(value,*par):
    return 10**(-np.log(value)*par[0] + par[1])

def starmodel3(value,*par):
    return 10**(-np.log(value**par[0])*par[1] + par[2])

def ChiSq2(parm, xval, yval, dy): # the weighted least-squares
    ymod = starmodel2(xval,*parm)
    chisq = sum(pow((yval-ymod)/dy,2))
    return chisq


In [36]:
# plot function
def bokehplotfunction(d,freq,flux,fluxerr,colour):
    lower = []
    upper = []
    base =[]
    for i in range(len(flux)):
        lower.append(flux[i]-fluxerr[i])
        upper.append(flux[i]+fluxerr[i])
        base.append(freq[i])

    d.scatter(freq,flux,color =colour)
    source_error = ColumnDataSource(data=dict(base=base, lower=lower, upper=upper))

    d.add_layout(
        Whisker(source=source_error, base="base", upper="upper", lower="lower")
    )
    return d

# make a fit
def fitexistingdata(freq,flux,fluxerr,ids,x):
    a=1
    b = 10
    c = 100
    p01=[b,c]
    ml_cfpars, ml_cfcovar = op.curve_fit(starmodel2, freq, flux, p01, sigma=fluxerr)
    err = np.sqrt(np.diag(ml_cfcovar))
    confidence = np.diag(ml_cfcovar)
    fit = starmodel2(x, *ml_cfpars)
    dof = len(freq)-len(p01)
    chisquare = ChiSq2(ml_cfpars,freq,flux,fluxerr)
    return fit,chisquare,dof

# get our own data
def getSourceData(d,runcat_id,colour):
    runcat = session.query(tkp.db.model.Runningcatalog).filter(tkp.db.model.Runningcatalog.id==runcat_id).one()
    sources = runcat.extractedsources
    
    flux = []
    fluxerr = []
    freq = []
    
    for s in sources:
        if s.extract_type == 0:
            flux.append(s.f_int*10**3)
            fluxerr.append(s.f_int_err*10**3)
            freq.append(s.image.freq_eff/(1.*10**6))

    bokehplotfunction(d,freq,flux,fluxerr,colour)
    return d



# initialize x
x = np.arange(1e1, 1e4, 1)

# loops through the data gathered sorting by id and plotting the fit
for i in dfFlux.id.unique():
    specid = dfFlux[dfFlux.id == i]
    ids = int(i)
    freq = np.array(specid.nu.astype(float))
    flux = np.array(specid.s_nu.astype(float))
    fluxerr = np.array(specid.e.astype(float))
    
    
#     Append catalogue data to the set:
    for j in FluxVar.instances:
        if j.id == ids:
            freq = np.append(freq,j.database.freq)
            flux = np.append(flux,j.database.pflux[j.entry]*10**3 )
            fluxerr = np.append(fluxerr,j.database.pfluxe[j.entry]*10**3 )

    print freq
    
    d = figure(title="ligthcurve for runcat %s" % ids, x_axis_label='freq', y_axis_label='flux',y_axis_type='log',x_axis_type='log')
    d = bokehplotfunction(d,freq,flux,fluxerr,"navy")
    
    try:
        fit,chisquare,dof = fitexistingdata(freq,flux,fluxerr,ids,x)
        d.line(x,fit,color='green')
    except:
        print "for id: %i there is no good fit" %ids
        print freq
    d = getSourceData(d,int(ids),colour="firebrick")
    
    show(d)
    try:
        print "with a goodness of fit of: %0.3f and a dof of: %0.1f" %(chisquare,dof)
    except:
        pass

[ 325.  1400.  1400.   365.   151.   151.   147.5   74. ]


with a goodness of fit of: 1.194 and a dof of: 6.0
[1400.   147.5   74. ]


with a goodness of fit of: 8.594 and a dof of: 1.0
[ 151.  1400.  1400.   325.   365.   151.  4850.    74.   151.   147.5
   74. ]


with a goodness of fit of: 17.555 and a dof of: 9.0
[365.  74.]


with a goodness of fit of: 25.000 and a dof of: 0.0
[1400.  365. 1400.  151.  325.   74.]


...

with a goodness of fit of: 1.668 and a dof of: 6.0
[365. 151.  74.]


with a goodness of fit of: 1.658 and a dof of: 1.0
[1400. 1400.  325.  365.   74.]


with a goodness of fit of: 1.317 and a dof of: 3.0
[1400.  325.  365.  151.   74.]


with a goodness of fit of: 1.242 and a dof of: 3.0
[ 365.  325.   74. 1400.  151.   74.]


with a goodness of fit of: 1.579 and a dof of: 4.0


In [38]:
for i in FluxVar.instances:
    if i.id == 15556:
        print "Data compared to " + i.database.name
        print i.id
        print websiteURL+str(i.id)
        print 'bananaflux: ' + str(i.pflux*i.scale)
        print i.database.name+'flux: ' + str(i.database.pflux[i.entry])
        print i.database.ra[i.entry]
        print i.database.dec[i.entry]
        print i.ra
        print i.dec
        print i.fk5
        print i.icrs
        print "------------------------"
        
#     if i.database == 'vssr':
        
#         print 'bananaflux: ' + str(i.pflux * vlssrscale)
#         print 'vlssrflux: ' + str(vssr.pflux[i.entry])
#         print "########################"
#     print vssr.ra[i.entry]
#     print vssr.dec[i.entry]
#     print i.ra
#     print i.dec

Data compared to vlssr
15556
http://banana.transientskp.org/r4/vlo_KmeulenTrap4P23/runningcatalog/15556
bananaflux: 1.2734638744252076
vlssrflux: 0.522
184.7767
48.5006
184.77692258
48.4988674497
12 19 06 +48 29 56
12 19 06 +48 29 56
------------------------


In [45]:
for i in dfFlux.id.unique():
    if i == "7605":
        specid = dfFlux[dfFlux.id == i]
        ids = int(i)
        freq = np.array(specid.nu.astype(float))
        flux = np.array(specid.s_nu.astype(float))
        fluxerr = np.array(specid.e.astype(float))
        ids = int(i)
        
print freq
print flux
print fluxerr

d = figure(title="ligthcurve for runcat %s" % ids, x_axis_label='freq', y_axis_label='flux',y_axis_type='log',x_axis_type='log')
d = bokehplotfunction(d,freq,flux,fluxerr,"navy")

try:
    fit,chisquare,dof = fitexistingdata(freq,flux,fluxerr,ids,x)
    d.line(x,fit,color='green')
except:
    print "for id: %i there is no good fit" %ids
    print freq
for j in FluxVar.instances:
    if j.id == ids:
        print 'hoi'
        print j.database.freq,j.database.pflux[j.entry]*10**3
        d.scatter(j.database.freq,j.database.pflux[j.entry]*10**3)
#         freq = np.append(freq,j.database.freq)
#         flux = np.append(flux,j.database.pflux[j.entry]*10**3 )
#         fluxerr = np.append(fluxerr,j.database.pfluxe[j.entry]*10**3 )
d = getSourceData(d,int(ids),colour="firebrick")

show(d)

[1400. 4850.   74.]
[ 100.   46. 2600.]
[ 20.    9.2 520. ]
hoi
74 2565.0


In [31]:

for i in range(len(tgss.pflux)):
    if tgss.pflux[i] <= 0.565 and tgss.pflux[i] >= 0.563:
        'hoi'
        print tgss.ra[i]
        print tgss.dec[i]
        
print '__________________'
for i in range(len(tgss.pflux)):
    if tgss.ra[i] >= 186.88 and tgss.ra[i] <=186.90:
        if tgss.dec[i] >= 44.96 and tgss.dec[i] <=44.98:
            print tgss.dec[i]
            print tgss.ra[i]
            print 'hoi'
            print tgss.pflux[i]

186.89523
44.97582
175.8606
41.6674
170.66138
47.90977
175.98412
58.714040000000004
204.02778999999998
46.87729
169.68031000000002
59.335930000000005
201.18626
39.56185
194.70323
63.88155
195.05472
66.26698
212.03564
41.11289
217.54735
47.21894
197.1843
28.9717
196.43546
25.06833
154.07204
36.16063
196.0842
23.469929999999998
216.63348
35.13708
226.59183
63.89281999999999
175.24049
22.28632
142.93352
44.53289
136.98233000000002
58.75286
210.80617
25.415210000000002
135.85545
49.80237
134.78691
51.86592
232.15419
73.35668000000001
140.44432
41.47168
227.41152999999997
77.72100999999999
181.62971000000002
14.95836
219.52499
82.20984
224.68568
29.974529999999998
205.45676
16.47241
192.94562
11.03726
231.02192999999997
29.006459999999997
102.07695
74.02501
145.40878
20.15458
__________________
44.97582
186.89523
hoi
0.5646


# PLOTTING

In [32]:
data = lif.Reader('asu.fit')
data

.1                               .2  .3      .4   [mJy]    MHz  \
0   ------   -  -------------------------------  --  ------  ------  -----   
1    50608   0  GB6 B1220+5043                   14   -1.16    6.26   4850   
2    50608   0  87GB 122025.7+504330             14   -1.16    6.26   4850   
3    50608   0  BWE 1220+5043                    14   -1.16    6.26   4850   
4    50608   0  4C +50.34                        14   -1.16    6.26    178   
5    50608   0  TXS 1220+507                     14   -1.16    6.26    365   
6    50608   0  WN B1220.4+5043                  14   -1.11    6.14    325   
7    50608   0  FIRST J122251.9+502655           14   -1.11    6.13   1400   
8    50608   0  NVSS J122251+502655              14   -1.11    6.14   1400   
9    50608   0  MY 122025.7+502701.2             14   -1.16    6.26    232   
10   50608   0  WB 1220+5043                     14   -1.23    6.41   1400   
11   50608   0  6C 122026+504332                 14   -1.11    6.14    151   
12   50608   0  6C 122025+504330                 14   -1.16    6.26    151   
13   50608   0  7C 122025.80+504334.00           14   -1.16    6.26    151   
14   50608   0  VLSS J1222.8+5026                14   -1.16    6.26     74   

          mJy     mJy.1       deg     deg.1    .5   .6         .7     arcsec  
0   ---------  --------  --------  --------  ----  ---  ---------  ---------  
1    7.60e+01   1.5e+01  185.7117  +50.4492  zSim  SED  Radio+Opt     108.00  
2    6.70e+01   1.3e+01  185.7158  +50.4481  zSim  SED  Radio+Opt     138.00  
3    6.40e+01   1.3e+01  185.7183  +50.4472  zSim  SED  Radio+Opt     138.00  
4    4.40e+03   1.3e+03  185.7208  +50.4467  zSim  SED  Radio+Opt     690.00  
5    2.29e+03   4.6e+02  185.7163  +50.4486  zSim  SED  Radio+Opt       6.00  
6    2.57e+03   5.1e+02  185.7162  +50.4486  zSim  SED  Radio+Opt      12.00  
7    4.50e+02   9.0e+01  185.7163  +50.4487  zSim  SED  Radio+Opt       5.00  
8    4.47e+02   8.9e+01  185.7163  +50.4488  zSim  SED  Radio+Opt      45.00  
9    4.34e+03   8.7e+02  185.7158  +50.4503  zSim  SED  Radio+Opt     150.00  
10   4.01e+02   8.0e+01  185.7183  +50.4472  zSim  SED  Radio+Opt     120.00  
11   5.53e+03   1.1e+03  185.7171  +50.4483  zSim  SED  Radio+Opt     252.00  
12   5.19e+03   1.0e+03  185.7163  +50.4478  zSim  SED  Radio+Opt     252.00  
13   5.29e+03   1.1e+03  185.7163  +50.4489  zSim  SED  Radio+Opt      70.20  
14   1.03e+04   2.1e+03  185.7167  +50.4481  zSim  SED  Radio+Opt      79.98

In [33]:

ra = data.deg[1:].astype(float)
flux = list(data.mJy[1:].astype(float))
freq = list(data.MHz[1:].astype(float))
fluxerr = list(data['mJy.1'][1:].astype(float))
print fluxerr
print flux
print freq

[15.0, 13.0, 13.0, 1300.0, 460.0, 510.0, 90.0, 89.0, 870.0, 80.0, 1100.0, 1000.0, 1100.0, 2100.0]
[76.0, 67.0, 64.0, 4400.0, 2290.0, 2570.0, 450.0, 447.0, 4340.0, 401.0, 5530.0, 5190.0, 5290.0, 10300.0]
[4850.0, 4850.0, 4850.0, 178.0, 365.0, 325.0, 1400.0, 1400.0, 232.0, 1400.0, 151.0, 151.0, 151.0, 74.0]


In [34]:

logspace = np.linspace(0,1e4,500)
from scipy.stats import linregress




In [35]:
runcat = session.query(tkp.db.model.Runningcatalog).filter(tkp.db.model.Runningcatalog.id==runcat_id).one()

sources = runcat.extractedsources

y = [(s.ra +360) for s in sources]
x = [s.f_int*10**3 for s in sources]
xerr = [s.f_int_err*10**3 for s in sources]
h = [s.image.freq_eff/(1.*10**6) for s in sources]


d = figure(title="ligthcurve for runcat %s" % runcat.id, x_axis_label='freq', y_axis_label='flux',y_axis_type='log',x_axis_type='log')
# p.scatter([x, y],[flux,ra],color=['firebrick','navy'])

d.scatter(h,x,color = 'firebrick')


lower = []
upper = []
base =[]
for i in range(len((x))):
    lower.append(x[i]-xerr[i])
    upper.append(x[i]+xerr[i])
    base.append(h[i])

source_error = ColumnDataSource(data=dict(base=base, lower=lower, upper=upper))

d.add_layout(
    Whisker(source=source_error, base="base", upper="upper", lower="lower")
)
lower = []
upper = []
base =[]
for i in range(len(flux)):
    lower.append(flux[i]-fluxerr[i])
    upper.append(flux[i]+fluxerr[i])
    base.append(freq[i])
# print freq
d.line(xfit,fit,color='green')

d.scatter(freq,flux,color ='navy')
source_error = ColumnDataSource(data=dict(base=base, lower=lower, upper=upper))

d.add_layout(
    Whisker(source=source_error, base="base", upper="upper", lower="lower")
)

# print x
# p.xaxis.formatter = DatetimeTickFormatter()
show(d)
print "goodness of fit of:" +str(ss.chi2.sf(chisquare, df=dof))

NameError: name 'xfit' is not defined

In [ ]:
print Transients.instances[0].pflux

In [ ]:
SavedPosSources(vars(Transients.instances[0]))

In [ ]:
print FluxVar.instances[0].fk5


In [ ]:
print PosVar.instances[0].pflux

In [ ]:
def reverseneg(ra):
    if ra<0:
        ra = ra +360
    return ra
pandacata['ra'] = pandacata.ra.apply(reverseneg)


In [ ]:

filtered_data = pandacata[(182.1 <= pandacata.ra) & (pandacata.ra<=188.5) &(49.8 <=pandacata.dec)&(pandacata.dec<=51.1)]
filtered_data = filtered_data.sort_values(by=['ra'])


In [ ]:
print len(tgsslist[0].ra)
print np.array(filtered_data.ra)

In [ ]:
PosVar.instances = []
print type(filtered_data['ra'].astype(float))

CheckSimOutsideDatabase(tgsslist[0],filtered_data,rcheck = 3,ycheck = 5,\
                     checklight = False, gamma = True,Cali = False,deruiter = True,euccutoff = .06)

In [ ]:
x = [s for s in filtered_data.ra]
y = [s for s in filtered_data.pflux]
xt = [s for s in tgsslist[0].ra]
yt = [s for s in tgsslist[0].pflux]

p = figure(title="ligthcurve for runcat %s" % runcat.id, x_axis_label='ra', y_axis_label='flux', x_axis_type='log')
# p.scatter([x, y],[flux,ra],color=['firebrick','navy'])
p.line(xt,yt,color ='navy')
p.line(x,y,color = 'firebrick')
show(p)